# Homework nr. 2 - data cleaning (deadline 8/11/2018)

In short, the main task is to clean The Metropolitan Museum of Art Open Access dataset.
  
> The instructions are not given in details: It is up to you to come up with ideas on how to fulfill the particular tasks as best you can. ;)

## What are you supposed to do:

  1. Download the dataset MetObjects.csv from the repository https://github.com/metmuseum/openaccess/.
  2. Check consistency of at least three features where you expect problems (include "Object Name" feature).
  3. Select some features where you expect integrity problems (describe your choice) and check integrity of those features.
  4. Convert at least five features to a proper data type. Choose at least one numeric, one categorical and one datetime.
  5. Find some outliers (describe your selection criteria).
  6. Detect missing data in at least three features, convert them to a proper representation (if they are already not), and impute missing values in at least one feature.

**If you do all this properly, you will obtain 6 points**

To earn **extra two points** you can do some of these:
  * Focus more precisely on cleaning of the "Medium" feature. Such if you like to use it in KNN based algorithms later.
  * Focus on the extraction of physical dimensions of each item (width, depth and height in centimeters) from the "Dimensions" feature.

## Comments

  * Please follow the instructions from https://courses.fit.cvut.cz/MI-PDD/homeworks/index.html.
  * If the reviewing teacher is not satisfied, he can give you another chance to rework your homework and to obtain more points.

In [1]:
import numpy as np
import pandas as pd
import sklearn as skit
from sklearn.cluster import KMeans
from sklearn.neighbors import NearestNeighbors
from scipy.stats import chi2_contingency
from IPython.display import display, Markdown, Latex

import seaborn as sns
import re

import matplotlib
import matplotlib.pyplot as plt
%matplotlib inline

In [2]:
df = pd.read_csv('openaccess/MetObjects.csv', low_memory=False)

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 472127 entries, 0 to 472126
Data columns (total 43 columns):
Object Number              472127 non-null object
Is Highlight               472127 non-null bool
Is Public Domain           472127 non-null bool
Object ID                  472127 non-null int64
Department                 472127 non-null object
Object Name                468155 non-null object
Title                      441060 non-null object
Culture                    192200 non-null object
Period                     73147 non-null object
Dynasty                    23304 non-null object
Reign                      11212 non-null object
Portfolio                  21840 non-null object
Artist Role                281379 non-null object
Artist Prefix              96627 non-null object
Artist Display Name        282598 non-null object
Artist Display Bio         235113 non-null object
Artist Suffix              10742 non-null object
Artist Alpha Sort          282569 non-null object


* All of Object ID are different is good set is as row index.

In [4]:
df.index = df['Object ID']

## Consistency check and repair
### Check consistency of "Object Name" attribute:

In [5]:
tmp = df['Object Name'].str.strip().str.len()
display(tmp.describe())
display(list(df.loc[tmp.nlargest(100).index]['Object Name']))
display(df.loc[tmp.nsmallest(100).index]['Object Name'])
display(list(df['Object Name'].unique()))

count    468155.000000
mean         10.244402
std           8.405991
min           0.000000
25%           5.000000
50%           7.000000
75%          12.000000
max          80.000000
Name: Object Name, dtype: float64

['Double-barreled flintlock shotgun with exchangeable percussion locks and barrels',
 'Nineteen ornamental fittings from a horse harness and an ornamental saddle plate',
 'Blade and for a hatchet (Nata) and mounting for a dagger (Chiisagatana-goshirae)',
 'Set of Pommel (Fuchigashira), Sword grip ornaments (Menuki), and Cord (Kurikata)',
 'Top two lames from a right thigh defense (Cuisse), possibly from armor for a boy',
 'Manuscript (Du Pré, Galliot (fl.1506 -1561) . [Miscelánea] [Manuscrito] . S.XVI)',
 'Plate 15. Descent into Hell; Christ carrying an episcopal cross, entering tPrint',
 'Pall, sheet, Wah, rather coarse, light weight, weft fringe, torn ends, very worn',
 'String of 16 spherical, 1 barrel and 1 cylindrical beads and 2 hippo head amulet',
 'Cone, round, Padiamunnebnesuttawy, chancellor, Amun, lector, priest Beniuutehhor',
 'Scarab, Menkheperra, nsw bit, royal title, mry imn, beloved of Amun, Thutmose II',
 'Cone, Ptahmose, circular impression, high priest of Amun, vizie

Object ID
49198     \r\n
267878    \r\n
378194    \r\n
479408    \r\n
24857       Ax
25577       Ax
32944       Ax
37759       Ax
38627       Ax
38628       Ax
38629       Ax
38630       Ax
38631       Ax
44826       Ax
50575       Ax
50576       Ax
50577       Ax
50594       Ax
50617       Ax
50618       Ax
50622       Ax
50624       Ax
50625       Ax
50626       Ax
50627       Ax
50629       Ax
50631       Ax
50632       Ax
50633       Ax
50634       Ax
          ... 
248056      As
248060      As
248062      As
254565      As
256803      As
500526      Ūd
500580      Po
500581      Po
500582      Lo
500583      Lo
500586      Lo
500587      Lo
500588      Po
500589      Bo
500590      Po
500606      Gu
500607      Gu
500608      Gu
500996      Ūd
501000      Ūd
501092      Ty
503203      Ūd
503211      So
503339      Em
503345      Ūd
503765      Se
504390      Ūd
504702      Yu
505449      Lo
546958      Ax
Name: Object Name, Length: 100, dtype: object

['Coin',
 'Peso',
 'Centavos',
 'Pesos',
 'Bust',
 'Clock',
 'Vase',
 'Side Chair',
 'Figure',
 'Advertisement',
 'Ale glass',
 'Andiron',
 'Apothecary jar',
 'Statuette',
 'Frame',
 'Architectural elements',
 'Loggia elements',
 'Bedroom',
 'Argand lamp',
 'Lamp shade',
 'Armchair',
 'Banister-back armchair',
 'Drawing',
 'Slat-back armchair',
 'Spindle-back armchair',
 'Teapot',
 'Rocking chair',
 'Reclining armchair',
 'Folding armchair',
 'Side chair',
 'Revolving armchair',
 'Furniture hardware',
 'Astral lamp',
 'Window',
 'Aviary',
 "Baby's bottle",
 'Badge',
 'Baking dish',
 'Balcony',
 'Ball',
 'Wall panel',
 'Baluster',
 'Banjo clock',
 'Bank',
 'Baptismal basin',
 'Baptismal bowl',
 'Baptismal certificate',
 'Bottle',
 'Mug',
 'Keg',
 'Basin',
 'Wash basin',
 'Basin Stand',
 'Basin stand',
 'Basket',
 'Door',
 'Oil cruet',
 'Beaker',
 'Pulque beaker',
 'Tumbler',
 'Bean pot',
 'Folding bedstead',
 'Bedstead',
 'Bell',
 'Bell pull',
 'Bellows',
 'Bench',
 'Sleigh seat',
 'Pai

* "Object Name" have a lot of name with \n or \r\n characters.
* In most of the cases I came across, these characters are instead of spaces.
* Second problem in data what I find is ? or (?). 
* This can be used as a result of some uncertainty about the "Object name", 
I will leave this information in data, but I will make the embarrassment consistent with char (?).
* After repair \r\n there is some empty char will replace with nan.
* There are some two char name which can be bad, but there is not documetation for data. I will not replace it.
* Repair consistency of "Object Name" below

In [6]:
q_mark2 = re.compile(r'[?]+')
end_line1 = re.compile(r'\r\n+')
end_line2 = re.compile(r'\n+')
spaces = re.compile(r'[ ]+')
df['Object Name'] = df['Object Name'].str.replace("\(\?\)", '?').str.replace(q_mark2, '(?)')
df['Object Name'] = df['Object Name'].str.replace(end_line1, '\n').str.replace(end_line2, ' ')
df['Object Name'] = df['Object Name'].str.replace(spaces, ' ').str.strip()
df['Object Name'].replace([''], np.nan, inplace=True)

### Next check attribute for consistency is "Dynasty". Here I indicated inconsistencies in the slashes used:

In [7]:
display(df['Dynasty'].unique())

array([nan, 'Dynasty 8–11', 'Dynasty 12', 'early Dynasty 18', 'Dynasty 1',
       'Dynasty 18, early', 'Dynasty 6', 'Dynasty 5', 'Dynasty 4–5',
       'Dynasty 5–6', 'Dynasty 4–mid 5', 'Dynasty 4, mid–5th Dynasty',
       'Dynasty 4', 'Dynasty 3', 'Dynasty 12–13', 'Dynasty 6, first half',
       'Dynasty 6–8', 'Dynasty 6-8', 'Dynasty 4-6', 'early Dynasty 3',
       'Dynasty 11-12', 'Dynasty 18', 'Dynasty 27', 'Dynasty 12–17',
       'Dynasty 17–Early Dynasty 18', 'Dynasty 17–18', 'mid-Dynasty 18',
       'late Dynasty 12–early 13', 'late Dynasty 12–early  Dynasty 13',
       'Dynasty 12, late - early 13', 'Dynasty 13', 'Dynasty 11',
       'Dynasty 12, late–early 13',
       'Dynasty 12, late-13 up to 1700 B. C.', 'Dynasty 13–17',
       'late Dynasty 12–early Dynasty 13',
       'Dynasty 12, late–13 up to 1700 B. C.', 'Dynasty 12, late–13',
       'Dynasty 9 or later', 'Dynasty 9–10', 'Dynasty 9–11', 'Dynasty 17',
       'Second Intermediate Period', 'Dynasty 12, late - 13 up to 1700'

* Especially 
    * 'Dynasty 12, late - early 13'
    * 'Dynasty 12, late–early 13'
    * 'early dynasty 4–5'
    * 'Dynasty 29'
* Word dynasty will be remove, because is in column name
* Convert ? -> (?)
* Conver string to lower case
* Remove th, st, etc. after numbers
* Repair this consistency problem below

In [8]:
q_mark2 = re.compile(r'[?]+')
end_line1 = re.compile(r'\r\n+')
end_line2 = re.compile(r'\n+')
spaces = re.compile(r'[ ]+')
number = df['Dynasty'].nunique()
th = re.compile(r"(?<=\d)(st|nd|rd|th)\b")

df['Dynasty'] = df['Dynasty'].str.lower().str.replace("dynasty", '').str.replace("dyn", '')
df['Dynasty'] = df['Dynasty'].str.replace("\(\?\)", ' ? ').str.replace(q_mark2, ' (?) ')
df['Dynasty'] = df['Dynasty'].str.replace(end_line1, '\n').str.replace(end_line2, ' ')
df['Dynasty'] = df['Dynasty'].str.replace(spaces, ' ').str.strip()
df['Dynasty'] = df['Dynasty'].str.replace("–", '-').str.replace("- ", '-').str.replace(' -', '-').str.strip()
df['Dynasty'] = df['Dynasty'].str.replace(th, '')

display(Markdown("After repair consistency of values the number of unique decrease from \
                 " + str(number) + " to " +  str(df['Dynasty'].nunique())))

After repair consistency of values the number of unique decrease from                  377 to 296

### Next check attribute for consistency is "Medium":

In [9]:
display(list(df['Medium'].unique()))

['Gold',
 'Silver',
 'Bronze or copper',
 'Nickel',
 'Pressed glass',
 'Mahogany, laminated',
 'Gold, amethysts, spessartites, tourmalines, fresh water pearls, quartzes, rock crystal, and enamel',
 'Oak, tulip poplar',
 'Earthenware, basalt',
 'Paper',
 'Brass, iron',
 'Brass',
 'Iron',
 'Bell metal',
 'Bell metal, possibly iron',
 'Iron, brass',
 'Brass, steel',
 'Wrought iron',
 'Brass and iron',
 'Bronze, glass, iron',
 'Earthenware',
 'Earthenware, lusterware',
 'Bronze',
 'Wood, gilt',
 'Wood',
 'Wood, marble',
 'Limestone, ceramic, and Fravrile glass',
 'Sheffield plate, earthenware, glass',
 'Bronze, gilt brass',
 'Gilt bronze',
 'Glass',
 'Oak',
 'Maple, ash',
 'Maple',
 'Hard maple, soft maple, ash',
 'Maple, oak',
 'Graphite on off-white wove paper',
 'Poplar, ash',
 'Maple, cottonwood',
 'Oak, spruce, maple',
 'Pine, ash, maple',
 'Hickory, pine',
 'Beech',
 'Ash',
 'Mahogany',
 'Walnut, white cedar, yellow pine',
 'Maple, birch',
 'Primary: mahogany.  Secondary: cherry (med

* Here is the inconsistency mostly in the font size of the names, the first letter is always big, so for example Iron, oak are different from Oak, iron.
* Another problem is again the characters for line breaks.
* Furthermore, there is two separators "," or "and"
* Repair this consistency problem below

In [10]:
end_line1 = re.compile(r'\r\n+')
end_line2 = re.compile(r'\n+')
spaces = re.compile(r'[ ]+')
df['Medium'] = df['Medium'].str.lower().str.replace(" and ", ',').str.replace(",,", ',')
df['Medium'] = df['Medium'].str.replace(end_line1, '\n').str.replace(end_line2, ' ')
df['Medium'] = df['Medium'].str.replace(', ', ',').str.replace(',', ', ')
df['Medium'] = df['Medium'].str.replace(spaces, ' ').str.strip()

## Features with integrity problems
1. I think that data integrity problem can be found for example for attributes "Object Begin Date" and "Object End Date". There end date should be bigger than the start date. These dates are represented by year as int64.

2. Next integrity problems could be in Artist attributes. In this attributes are values for more artists separated by "|", so when I have 3 authors separated, there should be  for each of "Role", "Nationality", "Begin Date", "End Data", etc.  exist same count of values separate with "|" too.

3. Next may be if the city is in the specific country, region ... But this is necessary check externally.

### Check "Object Begin Date" and "Object End Date" integrity:

In [11]:
display((df[(df['Object Begin Date'] > df['Object End Date'])])[['Object Name', 
                                                                 'Object Begin Date', 'Object End Date']].head(10))

number = (df[(df['Object Begin Date'] > df['Object End Date'])])[['Object Name', 
                                                                 'Object Begin Date', 'Object End Date']].shape[0]
display(Markdown("Number of row which has \"Object Begin Date\"\
                 bigger than \"Object End Date\" is " + str(number) + " of " + str(df.shape[0])))
display(Markdown("There are several ways to solve this problem. \
                 For example, by replacing \"Artist End Date\" with value from begin or set to NaN or delete this rows."))

Object Name  Object Begin Date  Object End Date
Object ID                                                       
38468                 Yaksha                -45              -55
55128                  Print               1861                9
107853                Dolman               1875             1800
209514                   Fan               1785             1779
229879     Sample and letter               1785             1773
237874             Fragments               1785             1779
243602      Ring with scarab                  0               -5
247380         Lebes gamikos               -399            -3000
249163          Neck-amphora               -450             -475
250013            Alabastron                  0               -4

Number of row which has "Object Begin Date"                 bigger than "Object End Date" is 198 of 472127

There are several ways to solve this problem.                  For example, by replacing "Artist End Date" with value from begin or set to NaN or delete this rows.

### Check Artists integrity problem:

In [12]:
x = lambda x: len(str(x).split("|")) if x is not np.nan else 0
number = df[((df['Artist Role'].apply(x) == df['Artist Display Name'].apply(x)) & 
       (df['Artist Display Bio'].apply(x) == df['Artist Alpha Sort'].apply(x)) &
       (df['Artist Begin Date'].apply(x) == df['Artist End Date'].apply(x)))].shape[0]

display(Markdown("Number of row where is OK the count of values in Artists atributes: " 
                 + str(number)))
display(Markdown("The value includes lines where all NaN values are present."))

Number of row where is OK the count of values in Artists atributes: 392990

The value includes lines where all NaN values are present.

## Convert features to a proper data type.
### Convert "Credit Line" to text ('Credit Line From') and year ('Credit Line Year') if it is possible:
### Convert "Credit Line Year" to data time type:


In [13]:
def split(x):
    x = str(x).split(",")[-1].strip()
    if x.isdigit(): return x
    else: return np.nan
def removeYear(x):
    y = str(x).split(",")[-1].strip()
    if y.isdigit(): return ",".join(str(x).split(",")[:-1])
    else: return x
    
df['Credit Line Year'] = df['Credit Line'].apply(split)
df['Credit Line From'] = df['Credit Line'].apply(removeYear)
df['Credit Line Year'] = pd.to_datetime(df['Credit Line Year'], format='%Y', errors='coerce')

### Convert "Department" to categorical type:

In [14]:
df['Department'] = df['Department'].astype('category')

### Convert "Metadata Date" to datetime category:

In [15]:
df['Metadata Date'] = pd.to_datetime(df['Metadata Date'], format='%m/%d/%Y %H:%M:%S %p')

In [172]:
test = 'h.3.5xw.36.2xl.72cm(h.1-3/8xw.14-1/4xl.28-3/8in.)'
test1 = 'overall:121.9x43.2x9.5cm(48x17x33/4in.)'
test2 = 'overall:121.9cmx43.2cmx9.5cm(48x17x33/4in.)'
test3 = 'h.3.5cmxw.36.2cmxl.72cm(h.1-3/8xw.14-1/4xl.28-3/8in.)'
test4 = 'h.3.5cmxw.36.2cm(h.1-3/8xw.14-1/4xl.28-3/8in.)'
test5 = 'h.3.5cmx(h.1-3/8xw.14-1/4xl.28-3/8in.)'


t3 = re.compile(r'(?:(h\.|w\.|l\.)*(\d*\.\d+|\d+)(cm|mm|m)*x)'+
                '(?:(h\.|w\.|l\.)*(\d*\.\d+|\d+)(cm|mm|m)*x)?'+
                '(?:(h\.|w\.|l\.)*(\d*\.\d+|\d+)(cm|mm|m)*)?')

#t2 = re.compile(r"[(](\d*\.\d+|\d+)x(\d*\.\d+|\d+)(cm)*[)]")
#t1 = re.compile(r"[(](\d*\.\d+|\d+)(cm)*[)]")
#g1 = re.compile(r"[(](\d*\.\d+|\d+)(g)*[)]")
reFind = [t3, t2, t1, g1]
for i in reFind:
    print(re.findall(i, test5))


[('h.', '3.5', 'cm', '', '', '', '', '', ''), ('', '8', '', '', '', '', 'w.', '14', ''), ('', '4', '', '', '', '', 'l.', '28', '')]
[]
[]
[]


In [116]:
#display(list(df['Dimensions'].unique()))
t3 = re.compile(r"[(](\d*\.\d+|\d+)(cm)*x(\d*\.\d+|\d+)(cm)*x(\d*\.\d+|\d+)(cm)*[)]")
t2 = re.compile(r"[(](\d*\.\d+|\d+)x(\d*\.\d+|\d+)(cm)*[)]")
t1 = re.compile(r"[(](\d*\.\d+|\d+)(cm)*[)]")
g1 = re.compile(r"[(](\d*\.\d+|\d+)(g)*[)]")
end_line1 = re.compile(r'\r\n+')
end_line2 = re.compile(r'\n+')
spaces = re.compile(r'[ ]+')

def tryGetSize(x):
    y = re.findall(t3, x)
    if len(y) > 0:
        return y[0][0], y[0][1], y[0][2]
    y = re.findall(t2, x)
    if len(y) > 0:
        return y[0][0], y[0][1], -1
    y = re.findall(t1, x)
    if len(y) > 0:
        return y[0][0], -1, -1
    return -1, -1, -1

def tryGetWeight(x):
    y = re.findall(g1, x)
    if len(y) > 0:
        return y[0][0]
    return -1

def getDim(x):
    # x, y, z, diam, weight
    sizes = [-1,-1,-1,-1,-1]
    y = x
    x = str(x).lower()
    x = re.sub(end_line1, '\n', x)
    x = re.sub(end_line2, ';', x)
    x = re.sub(spaces, '', x)
    x = x.replace('×', 'x')
    x = x.strip().split(';')
    
    for i in x:
        if 'diam.' in i:
            x1, y1, z1 = tryGetSize(i)
            if x1 == -1:
                print("FUCK_D - ", i)
                continue
            else:
                sizes[3] = x1
                continue
        if 'overall' in i:
            x1, y1, z1 = tryGetSize(i)
            if x1 == -1:
                print("FUCK_ALL - ", i)
                continue
            else:
                sizes[0] = x1
                if y1 != -1: sizes[1] = y1
                if z1 != -1: sizes[2] = z1
                continue
        if 'h.' in i:
            x1, y1, z1 = tryGetSize(i)
            if x1 == -1:
                print("FUCK_H - ", i)
                continue
            else:
                sizes[2] = x1
                continue
        if 'l.' in i:
            x1, y1, z1 = tryGetSize(i)
            if x1 == -1:
                print("FUCK_L - ", i)
                continue
            else:
                sizes[0] = x1 
        if 'w.' in i:
            x1, y1, z1 = tryGetSize(i)
            if x1 == -1:
                print("FUCK_W - ", i)
                continue
            else:
                sizes[1] = x1
                continue
        if 'g)' in i:
            g1 = tryGetWeight(i)
            if g1 == -1:
                print("FUCK_G - ", i)
                continue
            else:
                sizes[4] = g1 
                continue
        # Parse value
        x1, y1, z1 = tryGetSize(i)
        if x1 == -1:
            print("FUCKNEVIM - ", i)
            continue
        else:
            sizes[0] = x1
            if y1 != -1: sizes[1] = y1
            if z1 != -1: sizes[2] = z1
            continue
        #print("NICNEVIMFUCK - ", i)
    return "|".join(map(str, sizes))
temp = df['Dimensions'].apply(getDim)
#temp = df['Dimensions']
display(len(list(temp.unique())))
display(list(temp.unique()))

FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  13ft.9in.x24ft.21/2in.x50ft.91/2in.
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCK_ALL -  overall:73/4in.,220grams(19.7cm,7.073troyounces)
FUCK_ALL -  overall:71/2in.,223.7grams(19.1cm,7.192troyounces)
FUCK_ALL -  overall:77/16in.,184grams(18.9cm,5.916troyoun

FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  
FUCKNEVIM -  dimensionsunavailable
FUCK_D -  111/16in.diam.(4.3cmdiam.)
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCK_D -  base:diam.31/2in.(31/2in.)
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  103in(h)x60in(w)x12.5in(d)
FUCKNEVIM -  dimensionsnotavailable
FUCKNEVIM -  14x25x42ft.(168x300x504in.)
FUCKNEVIM -  3x601/2in.(7.6cmx153.7cm)
FUCKNEVIM -  35/8x17/8x17/8in.,212.9grams(9.2x4.8x4.8cm,6.845troyounces)
FUCKNEVIM -  dimensionsunavailable
FUCKNEVIM -  dimensionsunavailable
FUCK_H -  71/2in.h.(19.1cmh.)
FUCK_W -  w.53/4in.(14.cm)
FUCKNEVIM -  121/4x12in.(31.1cm

FUCKNEVIM -  37/8in.,312.9g(9.8cm,10oz,1dwt..)
FUCKNEVIM -  other(body):3in.,182.1g(7.6cm,5.855oz.)
FUCKNEVIM -  other(cover):11/16x49/16in.,130.8g(2.7x11.6cm,4.205oz.)
FUCKNEVIM -  dimensionsnotrecorded
FUCKNEVIM -  variousdimensions
FUCKNEVIM -  variousdimensions
FUCKNEVIM -  
FUCKNEVIM -  42ft.x18in.(504in.x45.7cm)
FUCKNEVIM -  42ft.x18in.(504in.x45.7cm)
FUCKNEVIM -  nan
FUCKNEVIM -  dimensionsnotrecorded
FUCKNEVIM -  dimensionsnotrecorded
FUCKNEVIM -  dimensionsnotrecorded
FUCKNEVIM -  dimensionsnotrecorded
FUCK_D -  41/2in.diam.(11.43cmdiam.)
FUCK_D -  43/8in.diam.(11.11cmdiam.)
FUCKNEVIM -  85/16x25x65in.,21999.5g(21.1x63.5x165.1cm,707.306oz.)
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  dimensionsunrecorded
FUCKNEVIM -  dimensionsunrecorded
FUCKNEVIM -  dimensionsunrecorded
FUCKNEVIM -  dimensionsunrecorded
FUCKNEVIM -  dimensionsunrecorded
FUCKNEVIM -  dimensionsunrecorded
FUCKNEVIM -  dimensionsunrecorded
FUCKNEVIM -  tieback:dimensionsunrecorded
FUCKNEVIM -  variousdimensions
FUC

FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  
FUCK_G -  wt.ofeagle,96lbs.(43.54kg)
FUCK_G -  wt.oftrunk,219lbs.(99.33kg)
FUCK_G -  wt.68lb.8oz.(31.07kg)
FUCK_G -  wt.50lb.7oz.(22.88kg)
FUCKNEVIM -  12.37.110
FUCKNEVIM -  12.37.111
FUCKNEVIM -  12.37.112
FUCKNEVIM -  12.37.113
FUCKNEVIM -  12.37.114
FUCKNEVIM -  12.37.115
FUCKNEVIM -  12.37.116
FUCKNEVIM -  12.37.117
FUCKNEVIM -  12.37.118
FUCKNEVIM -  12.37.119
FUCKNEVIM -  12.37.100
FUCKNEVIM -  12.37.101
FUCKNEVIM -  12.37.102
FUCKNEVIM -  12.37.103
FUCKNEVIM -  12.37.104
FUCKNEVIM -  12.37.105
FUCKNEVIM -  12.37.106
FUCKNEVIM -  12.37.107
FUCKNEVIM -  12.37.108
FUCK_W -  w.23/8in.(cm)
FUCKNEVIM -  12.37.109
FUCKNEVIM -  
FUCKNEVIM -  12.27.91
FUCKNEVIM -  12.27.92
FUCKNEVIM -  12.27.93
FUCKNEVIM -  12.27.94
FUCKNEVIM -  12.27.95
FUCKNEVIM -  12.27.96
FUCKNEVIM -  12.27.97
FUCKNEVIM -  12.27.98
FUCKNEVIM -  12.27.99
FUCKNEVIM -  
FUCKNEVIM -  12.37.85
FUCKNEVIM -  12.37.86
FUCKNEVIM -  12.37.87
FUC

FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  knife(c)
FUCKNEVIM -  fork(d)
FUCKNEVIM -  
FUCKNEVIM -  nan
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  nan
FUCKNEVIM -  hilt(a)
FUCKNEVIM -  blade(b)
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  
FUCK_G -  wt.34lb.8oz.(15.65kg)
FUCK_L -  cal..63in.(16.0mm)
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  27.159.10
FUCKNEVIM -  27.159.11
FUCKNEVIM -  27.159.14a
FUCKNEVIM -  27.159.14b
FUCKNEVIM -  27.159.14c
FUCKNEVIM -  27.159.14d
FUCKNEVIM -  27.159.14e
FUCKNEVIM -  27.159.13a
FUCKNEVIM -  27.159.13b
FUCKNEVIM -  27.159.13c
FUCKNEVIM -  27.159.13d
FUCKNEVIM -  27.159.13e
FUCK_G -  wt.61lb.10oz.(27.95kg)
FUCKNEVIM -  helmet(a)
FUCKNEVIM -  gorget(b)
FUCKNEVIM -  breastplate(c)
FUCKNEVIM -  backplate(d)
FUCKNEVIM -  rightpauldron(e)
FUCKNEVIM -  leftpau

...

FUCK_H -  th.0.7cm(1/4in.)
FUCK_H -  h.2cm(13/16in.)
FUCK_W -  w.1.4cm(9/16in.)
FUCK_H -  maximumth.1.2cm(1/2in.)
FUCK_H -  h.1.7cm(11/16in.)
FUCK_W -  w.1.8cm(11/16in.)
FUCK_H -  th.1.2cm(1/2in.)
FUCK_H -  h.1.5cm(9/16in.)
FUCK_W -  w.1.7cm(11/16in.)
FUCK_H -  th.0.7cm(1/4in.)
FUCK_H -  h.2cm(13/16in.n)
FUCK_W -  w.1.3cm(1/2in.)
FUCK_H -  th.0.8cm(5/16in.)
FUCK_H -  h.1.5cm(9/16in.)
FUCK_W -  w.1.3cm(1/2in.)
FUCK_H -  th.0.7cm(1/4in.)
FUCK_H -  h.1.7cm(11/16in.)
FUCK_W -  w.1.9cm(3/4in.)
FUCK_H -  th.1.3cm(1/2in.)
FUCK_H -  h.1.3cm(1/2in.)
FUCK_W -  w.1cm(3/8in.)
FUCK_H -  maximumth.0.7cm(1/4in.)
FUCK_H -  h.1.7cm(11/16in.)
FUCK_W -  w.1.3cm(1/2in.)
FUCK_H -  th.0.6cm(1/4in.)
FUCK_H -  h.1.9cm(3/4in.)
FUCK_W -  w.1.5cm(9/16in.)
FUCK_H -  th.1.1cm(7/16in.)
FUCK_H -  h.0.8cm(5/16in.)
FUCK_W -  w.0.9cm(3/8in.)
FUCK_H -  th.0.2cm(1/16in.)
FUCK_H -  h.1.2cm(1/2in.)
FUCK_W -  w.1cm(3/8in.)
FUCK_H -  th.0.9cm(3/8in.)
FUCK_H -  h.2.3cm(7/8in.)
FUCK_W -  w.2.2cm(7/8in.)
FUCK_H -  th.0.5cm(3/16

FUCKNEVIM -  24dx2.3h
FUCKNEVIM -  7dbasex3.6hcm
FUCKNEVIM -  15dx3.9hcm
FUCKNEVIM -  24dx3hcm
FUCKNEVIM -  3.42x4.42
FUCKNEVIM -  2.92x3.78cm
FUCKNEVIM -  4.57x3.78cm
FUCKNEVIM -  nan
FUCKNEVIM -  7.2x4.82cm
FUCKNEVIM -  2.78basex2.31
FUCKNEVIM -  15dx4.2h
FUCKNEVIM -  23dx21h
FUCK_D -  diam.0.45cm(3/16in)
FUCKNEVIM -  nan
FUCKNEVIM -  
FUCKNEVIM -  
FUCKNEVIM -  nan
FUCKNEVIM -  [8],244leavesofplates:chieflyillustrations(engravings),portrait
FUCKNEVIM -  volume:illustrations(somecolor)
FUCKNEVIM -  volume:illustrations(somecolor)
FUCKNEVIM -  volume:illustrations
FUCKNEVIM -  volume:illustrations
FUCKNEVIM -  seeattachedlist
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVI

FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCKNEVIM -  diameter(confirmed):41/16in.(103.4mm)
FUCKNEVIM -  image:ca.9.3x5.7cm
FUCKNEVIM -  mount:ca.10.0x6.0cm
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCK_L -  cal..38in.
FUCKNEVIM -  nan
FUCK_L -  cal.15/32in.(12mm)
FUCKNEVIM -  nan
FUCK_W -  w.6in.(15.3cm.)
FUCKNEVIM -  nan
FUCKNEVIM -  nan
FUCK_G -  confirmed:91/16x5x43/4in.,23.331oz.(23x12.7x12.1cm,661.5g)
FUCK_ALL -  6.3x10.7cm(overall)
FUCK_ALL -  6.3x10cm(overall)
FUCK_ALL -  6.2x10.1cm(overall)
FUCK_ALL -  6.2x10.2cm(overall)
FUCK_ALL -  6.3x10.5cm(overall)
FUCK_ALL -  6.1x10.6cm(overall)
FUCK_

133452

['-1|-1|-1|-1|-1',
 '-1|-1|-1|1.7|-1',
 '-1|-1|-1|1.3|-1',
 '-1|-1|-1|2.9|-1',
 '-1|-1|-1|1.9|-1',
 '-1|-1|-1|5.4|-1',
 '7|8.9|7|-1|-1',
 '61.9|37.1|13|-1|-1',
 '10.8|12.2|47.9|-1|600.1',
 '101.6|64.8|87.6|-1|-1',
 '-1|-1|30.5|-1|-1',
 '-1|-1|31.4|-1|-1',
 '27.9|22.9|-1|-1|-1',
 '-1|-1|16.7|7.6|-1',
 '-1|-1|15.9|7.5|-1',
 '78.4|63.5|35.2|-1|-1',
 '-1|-1|68.6|-1|-1',
 '-1|-1|40.6|-1|-1',
 '-1|-1|43.2|-1|-1',
 '-1|-1|29.2|-1|-1',
 '-1|-1|41.9|-1|-1',
 '-1|-1|58.4|-1|-1',
 '57.2|58.4|-1|-1|-1',
 '64.1|54.6|34.3|-1|-1',
 '-1|-1|59.7|-1|-1',
 '47|56.5|34.3|-1|-1',
 '53.3|53.3|34.3|-1|-1',
 '78.1|71.1|-1|-1|-1',
 '54|45.1|-1|-1|-1',
 '45.1|61|-1|-1|-1',
 '64.8|56.5|34.3|-1|-1',
 '41|38.7|20.6|-1|-1',
 '48.9|49.5|29.8|-1|-1',
 '52.7|49.5|29.8|-1|-1',
 '47.6|43.2|-1|-1|-1',
 '59.1|59.7|-1|-1|-1',
 '53.3|40|-1|-1|-1',
 '59.1|46.4|-1|-1|-1',
 '28.9|36.8|30.5|-1|-1',
 '47.6|44.5|27.3|-1|-1',
 '57.2|68.6|33|-1|-1',
 '61|29.2|40.6|-1|-1',
 '-1|-1|57.2|73.7|-1',
 '41|25.4|37.8|-1|-1',
 '47|43.2|-1|-

In [17]:
listt = [1,2,3,4]
print(listt[:-1])
#display(list(df['Dimensions'].unique()))

[1, 2, 3]


In [18]:
display(df.info())
display(df.nunique())

<class 'pandas.core.frame.DataFrame'>
Int64Index: 472127 entries, 1 to 816510
Data columns (total 45 columns):
Object Number              472127 non-null object
Is Highlight               472127 non-null bool
Is Public Domain           472127 non-null bool
Object ID                  472127 non-null int64
Department                 472127 non-null category
Object Name                468151 non-null object
Title                      441060 non-null object
Culture                    192200 non-null object
Period                     73147 non-null object
Dynasty                    23304 non-null object
Reign                      11212 non-null object
Portfolio                  21840 non-null object
Artist Role                281379 non-null object
Artist Prefix              96627 non-null object
Artist Display Name        282598 non-null object
Artist Display Bio         235113 non-null object
Artist Suffix              10742 non-null object
Artist Alpha Sort          282569 non-null objec

None

Object Number              469461
Is Highlight                    2
Is Public Domain                2
Object ID                  472127
Department                     19
Object Name                 27555
Title                      245972
Culture                      7183
Period                       1769
Dynasty                       296
Reign                         376
Portfolio                    3181
Artist Role                  6252
Artist Prefix                5526
Artist Display Name         60778
Artist Display Bio          44814
Artist Suffix                1697
Artist Alpha Sort           60784
Artist Nationality           3806
Artist Begin Date           23697
Artist End Date             24021
Object Date                 32210
Object Begin Date            2105
Object End Date              2078
Medium                      61051
Dimensions                 253620
Credit Line                 38688
Geography Type                132
City                         2663
State         